In [1]:
%load_ext autoreload
%autoreload 2

In [38]:
import matplotlib.pyplot as plt
import json
import os
import cv2
import time
import numpy as np
from csbdeep.utils import Path, normalize
from segmentation import MELC_Segmentation
import pandas as pd
import anndata as ad
import pickle
from initial_analysis import ExpressionAnalyzer

In [9]:
data = "ALS"

f = open('/data_slow/je30bery/spatial_proteomics/config.json')
config = json.load(f)
data_path = "/data_slow/je30bery/data/ALS"  #config[data]
seg = MELC_Segmentation(data_path, membrane_marker="cd45") 
# membrane_marker: str/None 
# radius: multiple of cell radius



Contact  Diagnose Sex   YOB   Consent/Date              Blood draw  \
PatID                                                                         
ALS01     Studer  3/1/2021   m  1968     12/14/2022  14.12.2022 / 10:15 Uhr   
ALS02  Wachsmann  4/1/2019   m  1982     12/14/2022  14.12.2022 / 11:30 Uhr   
ALS03     Studer  9/1/2022   w  1949     12/20/2022  20.12.2022 / 10:30 Uhr   
ALS04  Wachsmann  5/1/2021   m  1963  30.05.2023, E   30.05.2023/ 09:15 Uhr   

                   Comorbidities  
PatID                             
ALS01          Angststörung 2019  
ALS02       Kreuzbandruptur 2019  
ALS03                        NaN  
ALS04  Neuropathy, Diabetes 2021

In [73]:

for segment in ["nuclei", "cell"]:
    comorbidities = pd.read_csv("/data_slow/je30bery/data/ALS/ALS_comorbidities.txt", delimiter=";")
    comorbidities = comorbidities.set_index("PatID")

    EA = ExpressionAnalyzer()
    EA.run(segment=segment, profile=None)
    expression_data = EA.expression_data

    for fov in seg.fields_of_view:
        if "ipynb" in fov:
            continue

        adata = ad.AnnData(expression_data.loc[fov].iloc[:,:-2])
        adata.obs["cell_id"] = expression_data.loc[fov].index
        adata.obs["group"] = expression_data.loc[fov]["Group"]
        adata.obs["id"] = expression_data.loc[fov]["Sample"]
        sample = np.unique(expression_data.loc[fov]["Sample"])[0]

        if "ALS" in sample:
            for c in comorbidities.columns:
                adata.uns[str(c)] = comorbidities.loc[sample, c]

        seg.field_of_view = fov
        if os.path.exists(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_nuclei.pickle"):
            with open(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_nuclei.pickle", "rb") as handle:
                where_nuc = pickle.load(handle)
            with open(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_cell.pickle", "rb") as handle:
                where_cell = pickle.load(handle)
            nuc = np.load(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_nuclei.npy")
            cell = np.load(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_cells.npy")
        else:
            nuc, mem, where_nuc, where_mem = seg.run()

        markers = {
            m.split("_")[1]: os.path.join(seg.get_fov_dir(), m)
            for m in sorted(os.listdir(seg.get_fov_dir()))
            if m.endswith(".tif") and "phase" not in m
        }

        if "spatial" not in adata.uns:
            adata.uns["spatial"] = {}  # Create the "spatial" key if it doesn't exist

        if "images" not in adata.uns["spatial"]:
            adata.uns["spatial"]["images"] = {}  # Create the "images" key if it doesn't exist

        adata.uns["spatial"]["images"]["Propidium iodide"] = seg.get_prop_iodide()
        for m in markers:
            adata.uns["spatial"]["images"][str(m)] = cv2.imread(markers[m], cv2.IMREAD_GRAYSCALE)

        adata.uns["spatial"]["cell_id_coordinates"] = where_nuc if segment == "nuclei" else where_cell   
        adata.uns["spatial"]["cell_segmentation"] = nuc if segment == "nuclei" else cell
        # Assuming you have an AnnData object called 'adata'
        adata.write(f"/data_slow/je30bery/spatial_proteomics/{segment}_{fov}.h5ad")

        break

Calculating expression: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 36/36 [00:00<00:00, 526.36it/s]
anndata.py (117): Transforming to str index.


TypeError: Can't implicitly convert non-string objects to strings

Above error raised while writing key 'group' of <class 'h5py._hl.group.Group'> to /

In [74]:
adata

AnnData object with n_obs × n_vars = 5891 × 19
    obs: 'cell_id', 'group', 'id'
    uns: 'Contact', 'Diagnose', 'Sex', 'YOB', 'Consent/Date', 'Blood draw', 'Comorbidities', 'spatial'

np.load("/data_slow/je30bery/spatial_proteomics/segmentation_results/Healthy05 - 21334_cells.npy")

In [19]:
np.load("/data_slow/je30bery/spatial_proteomics/segmentation_results/Healthy05 - 21334_cells.npy")

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [59]:
expression_data.loc[fov]

CD11b-PE   CD16-PE  CD2-FITC   CD26-PE  CD29-FITC    CD3-PE  CD36-FITC  \
Index                                                                           
1      0.850394  0.976378  0.026247  0.000000   0.002625  0.013123   0.039370   
2      0.034031  0.688482  0.007853  0.013089   0.000000  0.036649   0.000000   
3      0.016611  0.627907  0.019934  0.000000   0.000000  0.000000   0.000000   
4      0.000000  0.634518  0.152284  0.000000   0.043147  0.000000   0.149746   
5      0.000000  0.000000  0.035422  0.000000   0.000000  0.000000   0.000000   
...         ...       ...       ...       ...        ...       ...        ...   
5887   0.244186  0.581395  0.023256  0.000000   0.000000  0.000000   0.220930   
5888   0.224199  0.035587  0.170819  0.000000   0.348754  0.000000   0.476868   
5889   0.974026  0.000000  0.090909  0.272727   0.175325  0.058442   0.402597   
5890   0.000000  0.000000  0.554667  0.704000   0.002667  0.226667   0.032000   
5891   0.013333  0.506667  0.000000  0.000000   0.000000  0.000000   0.013333   

        CD38-PE  CD4-PE   CD45-PE  ...   CD56-PE   CD57-PE    CD7-PE  \
Index                              ...                                 
1      0.000000     0.0  0.002625  ...  0.034121  0.000000  0.000000   
2      0.013089     0.0  0.028796  ...  0.060209  0.000000  0.180628   
3      0.292359     0.0  0.598007  ...  0.461794  0.737542  0.581395   
4      0.505076     0.0  0.017766  ...  0.170051  0.000000  0.649746   
5      0.000000     0.0  0.000000  ...  0.008174  0.000000  0.000000   
...         ...     ...       ...  ...       ...       ...       ...   
5887   0.709302     0.0  0.290698  ...  0.872093  0.000000  0.674419   
5888   0.352313     0.0  0.046263  ...  0.217082  0.000000  0.032028   
5889   0.305195     0.0  0.590909  ...  0.136364  0.000000  0.000000   
5890   0.000000     0.0  0.125333  ...  0.074667  0.000000  0.146667   
5891   0.000000     0.0  0.133333  ...  0.100000  0.526667  0.313333   

         CD8-PE  HLA-DQ-FITC  HLA-DR-PE  NeuN-AF488  PBS  Sample Group  
Index                                                                   
1      0.000000     0.020997   0.000000    0.099738  0.0   ALS01  Case  
2      0.002618     0.005236   0.000000    0.002618  0.0   ALS01  Case  
3      0.003322     0.136213   0.000000    0.039867  0.0   ALS01  Case  
4      0.000000     0.010152   0.000000    0.010152  0.0   ALS01  Case  
5      0.000000     0.024523   0.000000    0.027248  0.0   ALS01  Case  
...         ...          ...        ...         ...  ...     ...   ...  
5887   0.104651     0.000000   0.000000    0.302326  0.0   ALS01  Case  
5888   0.000000     0.010676   0.010676    0.149466  0.0   ALS01  Case  
5889   0.000000     0.370130   0.688312    0.357143  0.0   ALS01  Case  
5890   0.293333     0.024000   0.000000    0.058667  0.0   ALS01  Case  
5891   0.000000     0.000000   0.000000    0.013333  0.0   ALS01  Case  

[5891 rows x 21 columns]

In [56]:
adata.X

array([[0.8503937 , 0.97637795, 0.02624672, ..., 0.        , 0.09973753,
        0.        ],
       [0.03403141, 0.68848168, 0.0078534 , ..., 0.        , 0.0026178 ,
        0.        ],
       [0.0166113 , 0.62790698, 0.01993355, ..., 0.        , 0.03986711,
        0.        ],
       ...,
       [0.97402597, 0.        , 0.09090909, ..., 0.68831169, 0.35714286,
        0.        ],
       [0.        , 0.        , 0.55466667, ..., 0.        , 0.05866667,
        0.        ],
       [0.01333333, 0.50666667, 0.        , ..., 0.        , 0.01333333,
        0.        ]])

In [ ]:
plt.imshow(nuc)

In [ ]:
adata.X["nuclei"] = nuc

In [22]:
with open(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_nuclei.pickle", "rb") as handle:
    where_nuc = pickle.load(handle)
with open(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_cell.pickle", "rb") as handle:
    where_cell = pickle.load(handle)
nuc = np.load(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_nuclei.npy")
cell = np.load(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_cells.npy")

In [17]:
where_dict

{1: array([[1429, 1429, 1429, 1429, 1429, 1429, 1430, 1430, 1430, 1430, 1430,
         1430, 1430, 1430, 1430, 1430, 1430, 1431, 1431, 1431, 1431, 1431,
         1431, 1431, 1431, 1431, 1431, 1431, 1431, 1431, 1431, 1431, 1432,
         1432, 1432, 1432, 1432, 1432, 1432, 1432, 1432, 1432, 1432, 1432,
         1432, 1432, 1432, 1432, 1432, 1433, 1433, 1433, 1433, 1433, 1433,
         1433, 1433, 1433, 1433, 1433, 1433, 1433, 1433, 1433, 1433, 1433,
         1433, 1434, 1434, 1434, 1434, 1434, 1434, 1434, 1434, 1434, 1434,
         1434, 1434, 1434, 1434, 1434, 1434, 1434, 1434, 1434, 1435, 1435,
         1435, 1435, 1435, 1435, 1435, 1435, 1435, 1435, 1435, 1435, 1435,
         1435, 1435, 1435, 1435, 1435, 1435, 1435, 1435, 1436, 1436, 1436,
         1436, 1436, 1436, 1436, 1436, 1436, 1436, 1436, 1436, 1436, 1436,
         1436, 1436, 1436, 1436, 1436, 1436, 1436, 1437, 1437, 1437, 1437,
         1437, 1437, 1437, 1437, 1437, 1437, 1437, 1437, 1437, 1437, 1437,
         1437, 1437, 1

In [19]:
nuc = np.load(f"/data_slow/je30bery/spatial_proteomics/segmentation_results/{fov}_cells.npy")

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [36]:
comorbidities

Contact  Diagnose Sex   YOB   Consent/Date  PatID  \
0     Studer  3/1/2021   m  1968     12/14/2022  ALS01   
1  Wachsmann  4/1/2019   m  1982     12/14/2022  ALS02   
2     Studer  9/1/2022   w  1949     12/20/2022  ALS03   
3  Wachsmann  5/1/2021   m  1963  30.05.2023, E  ALS04   

               Blood draw              Comorbidities  
0  14.12.2022 / 10:15 Uhr          Angststörung 2019  
1  14.12.2022 / 11:30 Uhr       Kreuzbandruptur 2019  
2  20.12.2022 / 10:30 Uhr                        NaN  
3   30.05.2023/ 09:15 Uhr  Neuropathy, Diabetes 2021